In [671]:
import pandas as pd
import numpy as np
import panel as pn 
import altair as alt
import tqdm
import prot.viz
prot.viz.altair_theme()
pn.extension('vega')
_ = alt.data_transformers.enable('default')

from scipy import stats
# import matplotlib.pyplot as plt

from scipy.optimize import curve_fit
def func(x, a, c, d):
    return a*np.exp(-c*x)+d

# Schmidt et al. reported mass corrections
(c) 2020 The Authors. All creative work is published under a [CC-BY 4.0](https://creativecommons.org/licenses/by/4.0/) permissive license. All software is released under a standard [MIT](https://opensource.org/licenses/MIT) license. **This software is provided as-is and may be subject to change.**

In this notebook we look into one of the corrections that was applied by Schmidt *et al* in order to arrive at reasonable values of protein mass and copy numbers per cell. Specifically, in their work there was concern over the quality of using BCA as a reliable measure of total protein mass per cell. Indeed, their BCA measurements are rather noisy [provided to us by Alexander Schmidt via personal communication], and do not show a clear trend in total protein mass as a function of growth rate that might otherwise have been expected. We will show this below. To enable them to report somewhat more reasonable estimates of each protein across the growth conditions they invoked an assumption that the cellular protein concentration is relatively constant as a function of growth rate. There are two aspects to this that we want to consider more closely: 1) there is an apparent discrepency in the reported cell volumes that were used and the expected volumes based on work from the labs of people like Suckjoon Jun and Terence Hwa. 2) Whether the assumption that protein concentration is constant is indeed valid at high growth rates where ribosomal content and hence rRNA abundance is much higher. 


- I have been using the cell volumes predicted from the work using a mother machine. However, there does appear to be a notable difference in the volume predictions between this study and the later one using a turbidostat. Whether it is real or an experimental uncertainty is unclear and I’m tempted to either assume the ‘bulk’ measurement using a turbidostat is the correct one to consider for all the Schmidt data (or alternatively take an average). 
- First , it would be useful to plot the ‘raw’ total mass as a function of growth rate
- Then plot the corrected mass using the volumes from Heinamann, mother machine predictions, and turbidostat.
- Then, we can relax assumption that protein concentration is constant. Here I need to take care with my predictions on how protein mass and fraction of mass that is protein might increase with cell size. 

## Load in the data

In [672]:
# Load the original schmidt data 
data = pd.read_csv('../../data/schmidt2016_longform_annotated.csv')

# Load the correction details 
schmidt_corr = pd.read_csv('../../data/schmidt2016_raw_data/schmidt2016_correction_factors.csv')


In [673]:
data = data[data.dataset=='schmidt_2016']
data = data[data.growth_rate_hr >= 0]

## plotting of total mass data 

Let's begin by looking at the total protein mass across the conditions. First lets double check that the values provided by Alexander Schmidt match up with the numbers we have on hand.

In [674]:
data_tot = pd.DataFrame()
for c, d in data.groupby(['condition', 'growth_rate_hr']):
    tot_mass = d.reported_fg_per_cell.sum()
    d_list = {'reported_fg_per_cell' : tot_mass,
             'condition' : c[0],
             'growth_rate_hr' : c[1], 
              'dataset' : 'compiled  data; reported in SI'
             }
    data_tot = data_tot.append(d_list, 
                              ignore_index = True)

In [675]:
d = alt.Chart(data_tot).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('reported_fg_per_cell:Q', title = 'total mass per cell (fg)'),
    color = alt.Color('dataset:N'),
    )

schmidt_corr['dataset'] = 'numbers from Schmidt'
d_schmidt = alt.Chart(schmidt_corr).mark_point().encode(
        x = alt.X('experimental_growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('corrected_fg/cell:Q', title = 'total mass per cell (fg)'),
    color = alt.Color('dataset:N'),
    )


alt.layer(d, d_schmidt).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.LayerChart(...)

## Comparison of reported values versus those measured by SRM/ SID

It looks like I might now understand how these values were used - though perhaps not every detail. But in general, the proteome-wide absolute numbers are inferred based on the absolute quantitation that was performed on the 41 selected proteins. The 42 selected proteins were themselves quantified by doping in synthesized peptides (that reflect one of the peptides expected from each protein) and performing what is called  stable isotope dilution (SID) and selected reaction monitoring (SRM) LC-MS/MS analysis. Using the flow cytometry cell counts they could then determine the protein quantity per cell. As a starting point for the proteome-wide determination, they applied the more common strategy of shotgun liquid chromatography (LC)- MS, which resulted in condition-dependent intensities by label-free quantification (i.e. the intensity of the MS peaks reflects how much protein is there). They can then fit the absolute quantifications to the values obtained in the  label-free quantification and generate a calibration curve from which to infer the absolute abundance for all quantified proteins. Note that an important aspect here is that it makes no assumption that the signal intensity from the label-free quantification scales linearly to zero, which is an assumption that will exist in the other MS data sets we have.

Now in order to account for any potential protein loss during extraction, they did the following:

1) Performed a BCA analysis of their M9 minimal media + glucose condition to calculate the total protein mass per cell in this condition (again using the cell counts from the flow cytometry cell counting).

2) Using this as a reference, and assuming that total cellular protein concentration is roughly constant across growth conditions, they then estimated how the total protein content would change as a function of growth rate. This changes because the cells get larger as they grow faster, and information about cell volume was used to make this estimation. This provided the expected total protein per cell now in hand for all growth conditions

3) Now the expectation is that the total protein per cell should sum up to the value estimated above. My guess is that when they inferred the proteome-wide absolute measurements, they scaled the numbers such that the total protein mass matched the expected value. 

I think we can either get the exact 'correction' that was applied, or at least something close to it by comparing the absolute protein measurements from the SRM/SID analysis (reported in their SI Table 3 for Dataset 2), and the final reported absolute protein measurements (reported in their SI Table 5 for Dataset 2).


In [676]:
# load in Schmidt et al Table S3
data_s3 = pd.read_csv('../../data/schmidt2016_raw_data/schmidt2016_dataset_S3.csv')

# add in growth rates
growth_map = dict(zip(data.condition.unique(), data.growth_rate_hr.unique()))
data_s3['growth_rate_hr'] = data_s3.condition.map(growth_map)


In [677]:
data_s3_genes = data_s3.gene_name.unique()
data_trim = data[data.gene_name.isin(data_s3_genes)]
data_trim = pd.merge(data_trim, data_s3[data_s3.gene_name.isin(data_trim.gene_name.unique())][['tot_per_cell','condition', 'gene_name']], 
                     on = ['condition', 'gene_name'],
                     suffixes = ('','_sid'))

data_trim = data_trim.sort_values(by='growth_rate_hr')

In [678]:
data_trim[data_trim.condition == 'acetate'].head()

gene_name b_number condition  reported_tot_per_cell  reported_fg_per_cell  \
442      pykA    b1854   acetate                   1421              0.121144   
502      ybhA    b0766   acetate                    145              0.007269   
522       zwf    b1852   acetate                    625              0.057793   
22       aceF    b0115   acetate                   3567              0.391369   
122      fbaB    b2097   acetate                   4226              0.267341   

                                              go_terms             cog_class  \
442  GO:0005737; GO:1902912; GO:0016208; GO:0005515...            metabolism   
502  GO:0032361; GO:0016311; GO:0005829; GO:0046872...  poorly characterized   
522  GO:0016614; GO:0005515; GO:0042802; GO:0010699...            metabolism   
22   GO:0030523; GO:0016407; GO:0016746; GO:0016740...            metabolism   
122  GO:0005515; GO:0005737; GO:0042802; GO:0003824...            metabolism   

                              cog_category cog_letter  growth_rate_hr  \
442  carbohydrate transport and metabolism          G             0.3   
502       general function prediction only          R             0.3   
522  carbohydrate transport and metabolism          G             0.3   
22        energy production and conversion          C             0.3   
122  carbohydrate transport and metabolism          G             0.3   

                                          gene_product  reported_volume  \
442                                 pyruvate kinase II              2.3   
502  pyridoxal phosphate/fructose-1,6-bisphosphate ...              2.3   
522                              GLU6PDEHYDROG-MONOMER              2.3   
22   AceF-dihydrolipoate // "AceF-S-acetyldihydroli...              2.3   
122             fructose-bisphosphate aldolase class I              2.3   

     corrected_volume  tot_per_cell  fg_per_cell       dataset  \
442          0.375561   1293.466063     0.110271  schmidt_2016   
502          0.375561    131.986333     0.006617  schmidt_2016   
522          0.375561    568.906607     0.052606  schmidt_2016   
22           0.375561   3246.863790     0.356244  schmidt_2016   
122          0.375561   3846.718917     0.243347  schmidt_2016   

            dataset_name   strain  tot_per_cell_sid  
442  Schmidt et al. 2016  BW25113              1786  
502  Schmidt et al. 2016  BW25113               248  
522  Schmidt et al. 2016  BW25113               981  
22   Schmidt et al. 2016  BW25113              2143  
122  Schmidt et al. 2016  BW25113              4156

In [679]:
data_trim.head()

gene_name b_number        condition  reported_tot_per_cell  \
196      glcB    b2976  chemostat_u0.12                   1365   
296       mdh    b3236  chemostat_u0.12                  42300   
436       ppc    b3956  chemostat_u0.12                   1673   
136      fbaB    b2097  chemostat_u0.12                   4572   
516      ybhA    b0766  chemostat_u0.12                     14   

     reported_fg_per_cell                                           go_terms  \
196              0.182378  GO:0000287; GO:0005829; GO:0046872; GO:0016740...   
296              2.270639  GO:0019752; GO:0055114; GO:0016491; GO:0005975...   
436              0.275113  GO:0006107; GO:0000287; GO:0006099; GO:0003824...   
136              0.289229  GO:0005515; GO:0005737; GO:0042802; GO:0003824...   
516              0.000702  GO:0032361; GO:0016311; GO:0005829; GO:0046872...   

                cog_class                           cog_category cog_letter  \
196            metabolism       energy production and conversion          C   
296            metabolism       energy production and conversion          C   
436            metabolism       energy production and conversion          C   
136            metabolism  carbohydrate transport and metabolism          G   
516  poorly characterized       general function prediction only          R   

     growth_rate_hr                                       gene_product  \
196            0.12                                    MALSYNG-MONOMER   
296            0.12                               malate dehydrogenase   
436            0.12                    phosphoenolpyruvate carboxylase   
136            0.12             fructose-bisphosphate aldolase class I   
516            0.12  pyridoxal phosphate/fructose-1,6-bisphosphate ...   

     reported_volume  corrected_volume  tot_per_cell  fg_per_cell  \
196              1.9          0.308099   1231.588489     0.164553   
296              1.9          0.308099  38165.709211     2.048713   
436              1.9          0.308099   1509.485378     0.248224   
136              1.9          0.308099   4125.144740     0.260961   
516              1.9          0.308099     12.631677     0.000633   

          dataset         dataset_name   strain  tot_per_cell_sid  
196  schmidt_2016  Schmidt et al. 2016  BW25113              7560  
296  schmidt_2016  Schmidt et al. 2016  BW25113             39797  
436  schmidt_2016  Schmidt et al. 2016  BW25113              2667  
136  schmidt_2016  Schmidt et al. 2016  BW25113              5515  
516  schmidt_2016  Schmidt et al. 2016  BW25113                30

In [680]:
p = []

line_source = pd.DataFrame({'x' : np.linspace(1,100000, 100),
                            'y' : np.linspace(1,100000, 100)},
                          columns = ['x', 'y'])

for i, cond in enumerate(data_trim.condition.unique()):
    
    p_data = alt.Chart(data_trim[data_trim.condition == cond]).mark_point().encode(
        x = alt.X('reported_tot_per_cell:Q', title = 'copies per cell',
                 scale = alt.Scale(domain = [1,100000])),
        y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
                 scale = alt.Scale(domain = [1,100000])),
        color = alt.Color('condition:N')
        )
    
    p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
        x = 'x',
        y = 'y'
    )
    
    p_ = alt.layer(p_data, p_line).properties(
        title=cond,
        height=100,
        width=100
                )
    
    p = np.append(p, p_) 

alt.hconcat(alt.vconcat(p[0], p[1], p[2], p[3], p[4]),
            alt.vconcat(p[5], p[6], p[7], p[8], p[9]),
            alt.vconcat(p[10], p[11], p[12], p[13], p[14]),
            alt.vconcat(p[15], p[16], p[17], p[18], p[19])).configure_axis(
    labelFontSize=12,
    titleFontSize=12
    )

alt.HConcatChart(...)

In [681]:
p = []

line_source = pd.DataFrame({'x' : np.linspace(1,200000, 100),
                            'y' : np.linspace(1,200000, 100)},
                          columns = ['x', 'y'])

for i, cond in enumerate(data_trim.condition.unique()):
    
    p_data = alt.Chart(data_trim[data_trim.condition == cond]).mark_point().encode(
        x = alt.X('reported_tot_per_cell:Q', title = 'copies per cell',
                 scale = alt.Scale(type = 'log', domain = [1,200000])),
        y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
                 scale = alt.Scale(type = 'log', domain = [1,200000])),
        color = alt.Color('condition:N')
        )
    
    p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
        x = 'x',
        y = 'y'
    )
    
    p_ = alt.layer(p_data, p_line).properties(
        title=cond,
        height=100,
        width=100
                )
    
    p = np.append(p, p_) 
    
alt.hconcat(alt.vconcat(p[0], p[1], p[2], p[3], p[4]),
            alt.vconcat(p[5], p[6], p[7], p[8], p[9]),
            alt.vconcat(p[10], p[11], p[12], p[13], p[14]),
            alt.vconcat(p[15], p[16], p[17], p[18], p[19])).configure_axis(
    labelFontSize=12,
    titleFontSize=12
    )

alt.HConcatChart(...)

In [682]:
p = []

line_source = pd.DataFrame({'x' : np.linspace(1,200000, 100),
                            'y' : np.linspace(1,200000, 100)},
                          columns = ['x', 'y'])

for i, cond in enumerate(data_trim.condition.unique()):
    
    p_data = alt.Chart(data_trim[data_trim.condition == cond]).mark_point().encode(
        x = alt.X('tot_per_cell:Q', title = 'copies per cell',
                 scale = alt.Scale(type = 'log', domain = [1,200000])),
        y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
                 scale = alt.Scale(type = 'log', domain = [1,200000])),
        color = alt.Color('condition:N')
        )
    
    p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
        x = 'x',
        y = 'y'
    )
    
    p_ = alt.layer(p_data, p_line).properties(
        title=cond,
        height=100,
        width=100
                )
    
    p = np.append(p, p_) 
    
alt.hconcat(alt.vconcat(p[0], p[1], p[2], p[3], p[4]),
            alt.vconcat(p[5], p[6], p[7], p[8], p[9]),
            alt.vconcat(p[10], p[11], p[12], p[13], p[14]),
            alt.vconcat(p[15], p[16], p[17], p[18], p[19])).configure_axis(
    labelFontSize=12,
    titleFontSize=12
    )

alt.HConcatChart(...)

From the non-log plot above it looks like the faster growth rates deviate most from the dotted line (i.e. glycerol_pAA and LB_miller). I think this would suggest that a larger descrepency was calculated between the apparent total mass in the cell and the expected mass based on the BCA total protein analysis discussed above. 

From the log plot, it looks like the adjustment factor is just a factor that scale the data left of right on the horizontal axis. I wonder if we need to work in log space for this? In any case, it appears to me that indeed a larger 'correction' was applied to the glycerol_pAA and lb_miller data to make it consistent with the expectations for total cellular protein concentration. 

To make progress, lets try to repeat their copy number inference ourselves, beginning with the M9 minimal media glucose data.

In [683]:
data_glucose = data[data.condition == 'lb_miller']
data_glucose['rel_tot_per_cell'] = data_glucose['reported_tot_per_cell'] / (data_glucose['reported_tot_per_cell'].sum())

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [684]:
data_trim_glu = data_trim[data_trim.condition == 'lb_miller']
data_trim_glu['rel_tot_per_cell'] = data_trim_glu['reported_tot_per_cell'] / (data_glucose['reported_tot_per_cell'].sum())

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [685]:
glu = alt.Chart(data_trim_glu).mark_point().encode(
        x = alt.X('rel_tot_per_cell:Q', title = 'relative abundance (by copy number)',
                 scale = alt.Scale(type = 'log')),
        y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
                 scale = alt.Scale(type = 'log')),
        color = alt.Color('condition:N')
        )

glu.configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.Chart(...)

Okay, next we need to perform a linear regression to relate relative abundance to absolute units. 

In [686]:

slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(data_trim_glu.rel_tot_per_cell.values), 
                                            np.log(data_trim_glu.tot_per_cell_sid.values))

# slope, intercept, r_value, p_value, std_err = stats.linregress((data_trim_glu.rel_tot_per_cell.values), 
#                                             (data_trim_glu.tot_per_cell_sid.values))

# report coefficient of determination,  r**2
print("r-squared:", r_value**2)

r-squared: 0.8554579912069413


In [687]:
np.exp(intercept)

1869027.3025781536

In [688]:
glu = alt.Chart(data_trim_glu).mark_point().encode(
        x = alt.X('rel_tot_per_cell:Q', title = 'relative abundance (by copy number)',
                 scale = alt.Scale(type = 'log')),
        y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
                 scale = alt.Scale(type = 'log')),
        color = alt.Color('condition:N')
        )

glu.configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

x = np.linspace(data_trim_glu.rel_tot_per_cell.min(),data_trim_glu.rel_tot_per_cell.max(), 1000)

line_source = pd.DataFrame({'x' : x,
                            'y' : np.exp(np.log(x)*slope + intercept)},
                          columns = ['x', 'y'])

p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 1).encode(
    x = 'x',
    y = 'y'
)

alt.layer(glu, p_line).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    ).properties(
        height=300,
        width=300
        )

alt.LayerChart(...)

This looks good. Now I can use the regression line to predict the copy number per cell for all proteins in the proteome-wide dataset. From here I will then need to calculate total mass based on the molecular weight of each protein. Finally, I need to compare the summed mass to the expected mass determined by BCA. A final 'correction' factor will then be applied to scale the copy numbers such that the total mass is the expected value (with the assumption that a discrepency is due to protein extraction loss). 

In [689]:
np.exp(intercept*1.175 -np.exp(1))

1543880.1562141562

In [690]:
intercept*1.175 

16.968091215981108

In [691]:

data_glucose['rel_tot_per_cell'] = data_glucose['reported_tot_per_cell'] / (data_glucose['reported_tot_per_cell'].sum())

# data_glucose['tot_per_cell_pred'] = np.exp((np.log(data_glucose['rel_tot_per_cell'])*slope + intercept)*1.174 - np.log(np.exp(1)))
data_glucose['tot_per_cell_pred'] = np.exp((np.log(data_glucose['rel_tot_per_cell'])*slope + intercept))


/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/opt/anaconda3/lib/python3.7/site-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [692]:
x = np.linspace(1,
                data_glucose.tot_per_cell_pred.max(), 5000)

line_source = pd.DataFrame({'x' : x},
                          columns = ['x', 'y'])

p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 1).encode(
    x = 'x',
    y = 'x'
)


glu_all = alt.Chart(data_glucose[data_glucose.tot_per_cell_pred >0]).mark_point().encode(
        x = alt.X('reported_tot_per_cell:Q', title = 'reported copy number',
                 scale = alt.Scale(type = 'log')),
        y = alt.Y('tot_per_cell_pred:Q', title = 'MY prediction w/ SRM/SID data;',
                 scale = alt.Scale(type = 'log')),
        color = alt.Color('condition:N')
        )


l = alt.layer(glu_all, p_line).properties(
        height=300,
        width=300
        )

In [693]:
(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.HConcatChart(...)

I think I'm able to reproduce the Schmidt result. However, there are some aspects that need some thought. While a fit of the 31 absolute protein abundances to relative intensities does quite well, there is a skew to the predicted data as compared to the numbers that were reported in the SI (SI Table 5). It *almost* has a zero intercept, but not quite. Initially, my expectation was that I would have to scale the fit predictions to account for any protein extraction inefficiency. However, what appears to have been done is that the fit line was shifted to go through the zero intercept and then rescaled. This isn't totally unreasonable, since a prior expectation might have been that zero relative intensity should correspond to zero copies per cell. 
But alternatively, doesn't it defeat the purpose of performing those original absolute measurements to begin with? i.e. This is the same result we might have achieved without performing the SRM/ SIM step.

After some useful discussion with Griffin, I think the explanation might be that I'm trying to go through this data processing pipeline by renormalizing the reported copy numbers into relative intensities (from 0 to 1). This will not be equivalent to using the original raw mass spec. intensities obtained by the shotgun proteomics; the fitting based on the SRM/SIM step has already been applied and so the skew I see is a reflection of that. 

I think this also means I could back calculate the raw relative mass spec. intensities. Instead, I think an easier approach might be to just return to the comparison of the 31 proteins measured in absolute copy numbers by SRM/SIM and their reported copy numbers. The descrepency between these two numbers reflect the correction that was applied from the data. From the log-log plots, we can see that there is a translation in the line, and this shift was applied in order to ensure that the total protein concentration per cell matched their expectations.  

Next we need to figure out what that correction looks like. Specifically, there are two aspects that need to be dealt with. 

1. We do not think the cell volumes that were used are especially reasonable given the reported scaling 'law' for *E. coli*, which suggests cell volume should scale exponentially with growth rate. In using their cell volumes, 
the reported total mass appears to plateau as a function of growth rate, which does not seem quite right given the expected exponential scaling. 

2. We need to figure out how to deal with the expectation that protein concentration is likely decreasing as a function of growth rate. I'm not sure how precise can we be?

It is worthwhile to note that most of this data 'correction' will only have a major bearing on the two data points with high growth rate (LB_miller, glycerol_AA). 


As another note, we should also consider the possibility that there really wasn't a need to perform these corrections to the data. For example, if protein extraction efficiencies were not drastically different across the conditions, then using a single condition like M9 minimal media + glucose might bias all values toward any error associated with this single measurement. Lets first try to remove the corrections that were applied after estimating proteome-wide absolute numbers using the SRM/SID data.

In [694]:
# data_trim.cog_class.unique()
data_trim.head()

gene_name b_number        condition  reported_tot_per_cell  \
196      glcB    b2976  chemostat_u0.12                   1365   
296       mdh    b3236  chemostat_u0.12                  42300   
436       ppc    b3956  chemostat_u0.12                   1673   
136      fbaB    b2097  chemostat_u0.12                   4572   
516      ybhA    b0766  chemostat_u0.12                     14   

     reported_fg_per_cell                                           go_terms  \
196              0.182378  GO:0000287; GO:0005829; GO:0046872; GO:0016740...   
296              2.270639  GO:0019752; GO:0055114; GO:0016491; GO:0005975...   
436              0.275113  GO:0006107; GO:0000287; GO:0006099; GO:0003824...   
136              0.289229  GO:0005515; GO:0005737; GO:0042802; GO:0003824...   
516              0.000702  GO:0032361; GO:0016311; GO:0005829; GO:0046872...   

                cog_class                           cog_category cog_letter  \
196            metabolism       energy production and conversion          C   
296            metabolism       energy production and conversion          C   
436            metabolism       energy production and conversion          C   
136            metabolism  carbohydrate transport and metabolism          G   
516  poorly characterized       general function prediction only          R   

     growth_rate_hr                                       gene_product  \
196            0.12                                    MALSYNG-MONOMER   
296            0.12                               malate dehydrogenase   
436            0.12                    phosphoenolpyruvate carboxylase   
136            0.12             fructose-bisphosphate aldolase class I   
516            0.12  pyridoxal phosphate/fructose-1,6-bisphosphate ...   

     reported_volume  corrected_volume  tot_per_cell  fg_per_cell  \
196              1.9          0.308099   1231.588489     0.164553   
296              1.9          0.308099  38165.709211     2.048713   
436              1.9          0.308099   1509.485378     0.248224   
136              1.9          0.308099   4125.144740     0.260961   
516              1.9          0.308099     12.631677     0.000633   

          dataset         dataset_name   strain  tot_per_cell_sid  
196  schmidt_2016  Schmidt et al. 2016  BW25113              7560  
296  schmidt_2016  Schmidt et al. 2016  BW25113             39797  
436  schmidt_2016  Schmidt et al. 2016  BW25113              2667  
136  schmidt_2016  Schmidt et al. 2016  BW25113              5515  
516  schmidt_2016  Schmidt et al. 2016  BW25113                30

One other note that might be worth mentioning is that the genes they selected for SRM and SID are all essentially from the metabolism sector. Their absolute measurements indeed suggest that their numbers drop (or don't keep up with the general increase in copy number) with growth rate; especially for media like LB_miller. I worry that the use of these as reference points might have been a poor choice overall. Specifically, I doubt they provide a calibration curve across the entire range of copy numbers in the fast growth regime. So perhaps this is related to why the fast-growth copy numbers seem low overall?

Moving on. Lets first double check how the reported numbers compare to the SRM/SID measurements. I think they intercept zero, which means that in order to adjust the reported numbers to be consistent with the SRM/SID numbers, we need to only adjust the slope of the fit. 

In [695]:
cond = 'glucose'
data_cond = data[data.condition == cond]
data_cond['rel_tot_per_cell'] = data_cond['reported_tot_per_cell'] / (data_cond['reported_tot_per_cell'].sum())

data_cond_trim = data_cond[data_cond.gene_name.isin(data_s3_genes)]
data_cond_trim = pd.merge(data_cond, data_s3[data_s3.gene_name.isin(data_cond.gene_name.unique())][['tot_per_cell','condition', 'gene_name']], 
                     on = ['condition', 'gene_name'],
                     suffixes = ('','_sid'))

data_cond_trim = data_cond_trim.sort_values(by='growth_rate_hr')

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [696]:
# data_cond_trim['tot_per_cell_sid'] = data_cond_trim['tot_per_cell_sid']

In [697]:
# cond = 'glucose'
# data_trim_cond = data_trim[data_trim.condition == cond]
# data_trim_cond['rel_tot_per_cell'] = data_trim_cond['reported_tot_per_cell'] / (data_trim_cond['reported_tot_per_cell'].sum())

# perform regression
slope_abs, intercept_abs, r_value_abs, p_value, std_err = stats.linregress(np.log(data_cond_trim.reported_tot_per_cell.values), 
                                            np.log(data_cond_trim.tot_per_cell_sid.values))

# x = np.linspace(data_trim_cond.reported_tot_per_cell.min(),data_trim_cond.reported_tot_per_cell.max(), 1000)
x = np.linspace(1,200000, 100)

line_source_SRM = pd.DataFrame({'x' : x,
                            'y' : np.exp(np.log(x)*slope_abs + intercept_abs)},
                          columns = ['x', 'y'])

p_line_fit = alt.Chart(line_source_SRM).mark_line(strokeDash = [2,2], opacity = 1, color = 'red').encode(
    x = 'x',
    y = 'y'
)

In [698]:
line_source = pd.DataFrame({'x' : np.linspace(1,200000, 100),
                            'y' : np.linspace(1,200000, 100)},
                          columns = ['x', 'y'])

p_data = alt.Chart(data_cond_trim).mark_point().encode(
    x = alt.X('reported_tot_per_cell:Q', title = 'reported copies per cell',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    color = alt.Color('condition:N')
    )

p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
    x = 'x',
    y = 'y'
)

l = alt.layer(p_data, p_line, p_line_fit).properties(
    title=cond,
    height=300,
    width=300)


###############
slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(data_cond_trim.rel_tot_per_cell.values), 
                                            np.log(data_cond_trim.tot_per_cell_sid.values))
data_cond['tot_per_cell_pred'] = np.exp((np.log(data_cond['rel_tot_per_cell'])*slope + intercept))


p_data_all = alt.Chart(data_cond).mark_point().encode(
    x = alt.X('reported_tot_per_cell:Q', title = 'reported copies per cell',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    y = alt.Y('tot_per_cell_pred:Q', title = 'MY prediction of copies per cell',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    color = alt.Color('condition:N')
    )

r = alt.layer(p_data_all, p_line, p_line_fit).properties(
    title=cond,
    height=300,
    width=300)



####### plot 
(l | r).configure_axis(
    labelFontSize=12,
    titleFontSize=12
    )

/opt/anaconda3/lib/python3.7/site-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


alt.HConcatChart(...)

Hmm, I think the plot above suggests something a little more complicated. In any case, I think the way to get back their original values is to figure out how to transform the above fit line such that the predicted copy numbers go through the SRM/SID data with zero intercept.

In [699]:
#i.e. what is the transform required to get 
# np.log(data_cond['tot_per_cell_sid']) == (np.log(data_cond['reported_tot_per_cell'])*slope_abs + intercept_abs))
# np.log(data_cond['tot_per_cell_sid'])  - (np.log(data_cond['reported_tot_per_cell'])*slope_abs = intercept_abs

In [700]:
slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(data_cond_trim.reported_tot_per_cell.values), 
                                            np.log(data_cond_trim.tot_per_cell_sid.values))

data_cond_trim['tot_per_cell_pred_'] = np.exp((np.log(data_cond_trim['reported_tot_per_cell'])*slope + intercept))

slope_check, intercept_check, r_value, p_value, std_err = stats.linregress(np.log(data_cond_trim.tot_per_cell_pred_.values), 
                                            np.log(data_cond_trim.tot_per_cell_sid.values))
data_cond_trim['tot_per_cell_pred_check'] = np.exp((np.log(data_cond_trim['tot_per_cell_pred_'])*slope_check + intercept_check))

In [701]:
# x = np.linspace(data_trim_cond.reported_tot_per_cell.min(),data_trim_cond.reported_tot_per_cell.max(), 1000)
x = np.linspace(1,200000, 100)


line_source_SRM = pd.DataFrame({'x' : np.exp(np.log(x)*slope + intercept),
                            'y' : x},
                          columns = ['x', 'y'])

# p_line = alt.Chart(line_source_SRM).mark_line(strokeDash = [2,2], opacity = 1, color = 'red').encode(
#     x = 'x',
#     y = 'y'
# )

p_line_diag = alt.Chart(line_source_SRM).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
    x = 'y',
    y = 'y'
)

x_check = data_cond_trim.tot_per_cell_pred_.values
line_source_check = pd.DataFrame({'x_check' : x_check,
                            'y_check' : np.exp(np.log(x_check)*slope_check + intercept_check)},
                          columns = ['x_check', 'y_check'])

p_line_diag_check = alt.Chart(line_source_check).mark_line(strokeDash = [2,2], opacity = 0.5, color = 'red').encode(
    x = 'x_check',
    y = 'y_check'
)

p_data = alt.Chart(data_cond_trim).mark_point().encode(
    x = alt.X('tot_per_cell_pred_:Q', title = 'New prediction, copies per cell',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    y = alt.Y('tot_per_cell_sid:Q', title = 'copies per cell, SRM/SID',
             scale = alt.Scale(type = 'log', domain = [1,200000])),
    color = alt.Color('condition:N')
    )

alt.layer(p_data, p_line_diag, p_line_diag_check).properties(
    title=cond,
    height=300,
    width=300).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.LayerChart(...)

Okay, it looks like I can get make predictions of copy number that align with the SRM/SID measurements. Now lets go through and calculate what I think will be the original absolute copy numbers based on the SRM/SID data.

In [702]:
data_orig = pd.DataFrame()
data = data[data.dataset == 'schmidt_2016']
for c, d in data.groupby('condition'):
    if 'stationary' in c:
        continue
    # Perform fit to SRM/SID data using 31 proteins that were measured
    d_trim = d[d.gene_name.isin(data_s3_genes)]
    data_s3_temp = data_s3[data_s3.condition == c]
    d_trim = pd.merge(d_trim, data_s3_temp[data_s3_temp.gene_name.isin(d_trim.gene_name.unique())][['tot_per_cell','condition', 'gene_name']], 
                     on = ['condition', 'gene_name'],
                     suffixes = ('','_sid'))
#     print(d_trim.head())
#     break
    slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(d_trim.reported_tot_per_cell.values), 
                                                np.log(d_trim.tot_per_cell_sid.values))
    
    # Transform 'reported_tot_per_cell' using this fit
    d['tot_per_cell_pred_'] = np.exp((np.log(d['reported_tot_per_cell'])*slope + intercept))

    # Append to DataFrame
    data_orig = data_orig.append(d, 
                                ignore_index = True)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


Now lets take a look at total protein mass per cell

In [703]:
# I think this is a quick way to get fg
data_orig['fg_per_cell_pred_'] = data_orig['tot_per_cell_pred_'] * (data_orig['reported_fg_per_cell']/data_orig['reported_tot_per_cell'])

source = pd.DataFrame()
for c, d in data_orig.groupby('condition'):
    data_list = {'growth_rate' : d.growth_rate_hr.unique(),
    'fg_per_cell' : d.fg_per_cell_pred_.sum()}
    
    source = source.append(data_list,
                           ignore_index = True)
    


In [704]:
alt.Chart(source).mark_point().encode(
    x = alt.X('growth_rate:Q', title = 'growth rate (hr-1)'),
    y = alt.Y('fg_per_cell:Q', title = 'mass per cell (fg)'),
    color = alt.Color('condition:N')
    ).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.Chart(...)

This doesn't look good! The total mass per cell is slowly droping. While I didn't expect things to look perfect, this isn't what I had in mind - i.e. I expected the total mass to still increase with growth rate. Perhaps I am thinking about this incorrectly. Specifically, maybe I DO need to consider the total protein mass and not just the copy number. 

In [705]:
data.condition.unique()

array(['lb_miller', 'glycerol_pAA', 'acetate', 'fumarate', 'galactose',
       'glucose', 'glucosamine', 'glycerol', 'pyruvate', 'succinate',
       'fructose', 'mannose', 'xylose', 'osmotic_stress_glucose', '42C',
       'pH6', 'chemostat_u0.12', 'chemostat_u0.2', 'chemostat_u0.35',
       'chemostat_u0.5'], dtype=object)

In [706]:
cond = 'glucose'
data_cond = data[data.condition == cond]
data_cond['rel_tot_per_cell'] = data_cond['reported_tot_per_cell'] / (data_cond['reported_tot_per_cell'].sum())

data_cond_trim = data_cond[data_cond.gene_name.isin(data_s3_genes)]
data_cond_trim = pd.merge(data_cond, data_s3[data_s3.gene_name.isin(data_cond.gene_name.unique())][['tot_per_cell','condition', 'gene_name']], 
                     on = ['condition', 'gene_name'],
                     suffixes = ('','_sid'))

data_cond_trim['fg_per_cell_sid'] = data_cond_trim['tot_per_cell_sid'] * (data_cond_trim['fg_per_cell']/data_cond_trim['tot_per_cell'])

line_source = pd.DataFrame({'x' : np.linspace(0.01,10, 100),
                            'y' : np.linspace(0.01,10, 100)},
                          columns = ['x', 'y'])

p_line = alt.Chart(line_source).mark_line(strokeDash = [2,2], opacity = 0.5).encode(
    x = 'x',
    y = 'y'
)
###############

p_data = alt.Chart(data_cond_trim).mark_point().transform_calculate(
        shift = 'datum.reported_fg_per_cell'
    ).encode(
    x = alt.X('shift:Q', title = 'reported fg per cell',
             scale = alt.Scale(type = 'log')),
    y = alt.Y('fg_per_cell_sid:Q', title = 'fg per cell, SRM/SID',
             scale = alt.Scale(type = 'log')),
    color = alt.Color('condition:N')
    )

alt.layer(p_line, p_data)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


alt.LayerChart(...)

Now lets try to determine shift in reported fg per cell to get it to match SRM/SID

In [707]:
slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(data_cond_trim.reported_fg_per_cell.values), 
                                            np.log(data_cond_trim.fg_per_cell_sid.values))

data_cond_trim['fg_per_cell_pred_'] = np.exp((np.log(data_cond_trim['reported_fg_per_cell'])*slope + intercept))



In [708]:
x_check = data_cond_trim.reported_fg_per_cell.values
line_source_check = pd.DataFrame({'x_check' : x_check,
                            'y_check' : np.exp(np.log(x_check)*slope + intercept)},
                          columns = ['x_check', 'y_check'])

p_line_diag_check = alt.Chart(line_source_check).mark_line(strokeDash = [2,2], opacity = 0.5, color = 'red').encode(
    x = 'x_check',
    y = 'y_check'
)

In [709]:
alt.layer(p_line, p_data, p_line_diag_check)

alt.LayerChart(...)

In [710]:
data_orig_fg = pd.DataFrame()
data = data[data.dataset == 'schmidt_2016']
for c, d in data.groupby('condition'):
    if 'stationary' in c:
        continue
    # Perform fit to SRM/SID data using 31 proteins that were measured
    d_trim = d[d.gene_name.isin(data_s3_genes)]
    data_s3_temp = data_s3[data_s3.condition == c]
    d_trim = pd.merge(d_trim, data_s3_temp[data_s3_temp.gene_name.isin(d_trim.gene_name.unique())][['tot_per_cell','condition', 'gene_name']], 
                     on = ['condition', 'gene_name'],
                     suffixes = ('','_sid'))
    d_trim['fg_per_cell_sid'] = d_trim['tot_per_cell_sid'] * (d_trim['fg_per_cell']/d_trim['tot_per_cell'])

#     break
    slope, intercept, r_value, p_value, std_err = stats.linregress(np.log(d_trim.reported_fg_per_cell.values), 
                                                np.log(d_trim.fg_per_cell_sid.values))
    
    # Transform 'reported_tot_per_cell' using this fit
    d['fg_per_cell_pred_'] = np.exp((np.log(d['reported_fg_per_cell'])*slope + intercept))

    # Append to DataFrame
    data_orig_fg = data_orig_fg.append(d, 
                                ignore_index = True)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [711]:
source = pd.DataFrame()
for c, d in data_orig_fg.groupby('condition'):
    data_list = {'growth_rate' : d.growth_rate_hr.unique(),
    'fg_per_cell' : d.fg_per_cell_pred_.sum()}
    
    source = source.append(data_list,
                           ignore_index = True)
    

In [712]:
alt.Chart(source).mark_point().encode(
    x = alt.X('growth_rate:Q', title = 'growth rate (hr-1)'),
    y = alt.Y('fg_per_cell:Q', title = 'mass per cell (fg)'),
    color = alt.Color('condition:N')
    ).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.Chart(...)

# Correction Approach 1. 

1. Correction 1: Assume a different set of cell volumes for these growth rates

2. Correction 2: Assume that protein concentration is not constant.



## Correction 1: Assume that protein concentration is constant, but use different cell volumes.

I've actually worked through some of this in another notebook. Lets add it in here.


The volume-growth rate scaling that has been demonstrated for bacteria, and particularly nicely for $E. coli$ in Suckjoon Jun's lab, shows that cell volume, $V$, increases exponentially,

\begin{equation*}
V = S_0 \cdot 2^{\tau_{cyc} / \tau}.
\end{equation*}

where $S_0$ can be considered as the smallest 'unit cell' for the growing bacterium, $\tau_{cyc}$ is the time period of the cell cycle (combined process of chromosome replication and cell division), while $\tau$ is the average doubling time. Note that the growth rate of the cell is given by $\lambda = ln(2)/\tau$. In the work of Taheri-Araghi et al., they used a microfluidic mother machine to vary growth rate (via nutrient conditions) and reported the volume scaling as,

\begin{equation*}
V = 0.27 \cdot 2^{1.1 \cdot \lambda}.
\end{equation*}

In a more recent effort, the same lab also performed related work but where they instead were growing cells in a turbidostat (i.e. bulk growth instead of in a microfluidic device) [Si et al.]. It's unclear why and if those two approaches should lead to a different result, but the empirical fit nonetheless provides a different prediction. Specifically, in that work the data follows a scaling given by,


\begin{equation*}
V = 0.28 e^{1.33 \cdot \lambda}.
\end{equation*}
Here I use an exponential instead of a 2 to match the equation shown in their paper. Of note is that it does predict a cell volume which is slightly larger than the Taheri-Araghi et al. prediction. The smallest cell size is essentially the same. 

In [713]:
growth_rate = np.linspace(0,2.2, 100)
vol_TA = 0.27 * 2**(1.1  * growth_rate / np.log(2))
vol_Si = 0.28 * np.exp(1.33  * growth_rate)
vol = np.append(vol_TA, vol_Si)
growth_rate = np.append(growth_rate,growth_rate)
label = np.append(['Taheri-Araghi et al. 2015' for i in np.arange(100)], ['Si et al. 2017' for i in np.arange(100)])

source = pd.DataFrame({'growth rate' : growth_rate,
                     'vol' : vol,
                     'label' : label},
                     columns = ['growth rate', 'vol', 'label'])


r = alt.Chart(source).mark_line().encode(
        x = alt.X('growth rate:Q', title = 'growth rate'),
        y = alt.Y('vol:Q', title = 'cell volume (fL)',
                 scale = alt.Scale(type = 'log')),
        color = alt.Color('label:N')
        ).properties(
        height=300,
        width=300
        )


l = alt.Chart(source).mark_line().encode(
        x = alt.X('growth rate:Q', title = 'growth rate'),
        y = alt.Y('vol:Q', title = 'cell volume (fL)'),
        color = alt.Color('label:N')
        ).properties(
        height=300,
        width=300
        )

(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16
    )

alt.HConcatChart(...)

Lets also plot the data associated with these two curves. In addition, I would also like to add in the volumes that were measured in Basan et al. 2015. Note that these differ quite substantially, but this is due to uncertainty in measuring the short axis cell width. Otherwise, the logarithmic scaling is observed. 

In [714]:
# Si et al. 2017, X = growth rate lambda (hr-1), Y = cell size/volume (um^3)

[lambda_Si, vol_Si] = np.array(\
           [[0.363963963963964, 0.45043900416067056],
            [0.6234234234234235, 0.608559072706366],
            [0.6450450450450451, 0.611779810530591],
            [0.6450450450450451, 0.6021683748802841],
            [0.7027027027027026, 0.5682004227055784],
            [0.7603603603603606, 0.533326007698337],
            [0.7711711711711713, 0.5059047663020904],
            [1.055855855855856, 0.8946391099114556],
            [1.0990990990990992, 0.9838096192820653],
            [1.0306306306306308, 1.0371344401875353],
            [1.01981981981982, 1.042623370137201],
            [1.0990990990990992, 1.0933495931947346],
            [1.10990990990991, 1.2945410325726456],
            [1.156756756756757, 1.301392261082108],
            [1.156756756756757, 1.2410138473232424],
            [1.257657657657658, 1.3719308163979327],
            [1.3153153153153156, 1.3503769427141221],
            [1.347747747747748, 1.1834367049081955],
            [1.5063063063063065, 1.423570584262022],
            [1.5063063063063065, 1.624385051892262],
            [1.5063063063063065, 1.615833415686422],
            [1.5639639639639642, 1.615833415686422],
            [1.812612612612613, 2.7537778338617485],
            [1.7693693693693697, 3.2605110229259635],
            [1.7117117117117122, 3.2605110229259635],
            [1.7081081081081082, 3.4191430027642107],
            [1.7585585585585586, 3.901460767294091],
            [1.9387387387387391, 3.2605110229259635],
            [1.9495495495495498, 3.4737172287135545],
            [2.1189189189189195, 4.178577227097599]]).T

# Taheri-Araghi et al. 2015; X = # divisions per hr (so need to divide by ln(2) to get lambda)
                               # Y = cell size/ volume in um^3
                               
[division_rate_TA, vol_TA] = np.array(\
            [[0.7879988432620013, 0.6122987709420634],
            [0.8047860034702141, 0.6527558488549048],
            [1.2891736552920765, 0.8659212260906433],
            [1.7678896761133602, 1.1672203351966055],
            [2.07753036437247, 1.4996391395886446],
            [2.5784665991902838, 2.38476342463309],
            [3.5812066223250443, 3.9365261908448455]]).T

lambda_TA = division_rate_TA * np.log(2)

# Basan et al. 2015   X = growth rate lambda (hr-1), Y = cell size/volume (um^3)                 
[lambda_basan, vol_basan] = np.array(\
             [[0.4198116303491731, 1.3712424520871629],
            [0.4703662378577056, 1.7014472302441597],
            [0.6994494946180101, 1.7050406930953006],
            [0.9825454515620897, 2.3447755316356],
            [1.2942537411394068, 3.3379003675505388],
             [1.84057085192964, 6.617058283013914]]).T

In [715]:
# lets also determine a line of best fit for the Basan et al. data (use provided fit for others)

from scipy.optimize import curve_fit
def func(x, a, c, d):
    return a*np.exp(-c*x)+d

popt_vol, pcov_vol = curve_fit(func, lambda_vol, vol, p0=(1, 1e-6, 1))


# lets just take average of all data
lambda_avg = np.append(np.append(lambda_Si, lambda_TA), lambda_basan)
lambda_avg = np.sort(lambda_avg)
lambda_sort_ind = np.argsort(lambda_avg)
vol_avg_ = np.append( np.append(vol_Si, vol_TA), vol_basan)
vol_avg = [vol_avg_[i] for i in lambda_sort_ind ]

popt_vol_avg, pcov_vol_avg = curve_fit(func, lambda_avg, vol_avg, p0=(1, 1e-6, 1))


# slope_basan, intercept_basan, r_value, p_value, std_err = stats.linregress(np.log(vol_basan), 
#                                             lambda_basan)

ValueError: operands could not be broadcast together with shapes (6,) (200,) 

In [ ]:
lambda_avg

In [716]:

# combine datasets into one DataFrame
source_data = pd.DataFrame({'growth_rate_hr' : lambda_Si,
                        'vol_um3' : vol_Si, 
                        'dataset' : ['Si et al. 2017' for i in np.arange(len(vol_Si))]},
                     columns = ['growth_rate_hr', 'vol_um3',
                               'dataset'])
source_data = source_data.append(\
            pd.DataFrame({'growth_rate_hr' : lambda_TA,
                        'vol_um3' : vol_TA, 
                        'dataset' : ['Taheri-Araghi et al. 2015' for i in np.arange(len(vol_TA))]},
                         columns = ['growth_rate_hr', 'vol_um3',
                               'dataset']))
source_data = source_data.append(\
                pd.DataFrame({'growth_rate_hr' : lambda_basan,
                        'vol_um3' : vol_basan, 
                        'dataset' : ['Basan et al. 2015' for i in np.arange(len(vol_basan))]}, 
                        columns = ['growth_rate_hr', 'vol_um3',
                               'dataset']))

# add in schmidt info
data_condition = data[data.growth_rate_hr >= 0].sort_values(by='growth_rate_hr', ascending=True).condition.unique()
lambda_dict = dict(zip(data.condition,data.growth_rate_hr))
vol_dict = dict(zip(data.condition,data.reported_volume))
source_data = source_data.append(\
                pd.DataFrame({'growth_rate_hr' : [lambda_dict[c] for c in data_condition],
                        'vol_um3' : [vol_dict[c] for c in data_condition], 
                        'dataset' : ['Schmidt et al. 2016' for i in np.arange(len(data_condition))]}, 
                        columns = ['growth_rate_hr', 'vol_um3',
                               'dataset']))


In [717]:
# combine predictions into one DataFrame
x = np.linspace(0,2.5,150)
source_pred = pd.DataFrame({'growth_rate_hr' : x,
                        'vol_um3' : 0.28 * np.exp(1.33  * x), 
                        'dataset' : ['Si et al. 2017' for i in np.arange(len(x))]},
                     columns = ['growth_rate_hr', 'vol_um3',
                               'dataset'])
source_pred = source_pred.append(\
            pd.DataFrame({'growth_rate_hr' : x,
                        'vol_um3' : 0.27 * 2**(1.1  * x / np.log(2)), 
                        'dataset' : ['Taheri-Araghi et al. 2015' for i in np.arange(len(x))]},
                         columns = ['growth_rate_hr', 'vol_um3',
                               'dataset']))
source_pred = source_pred.append(\
                pd.DataFrame({'growth_rate_hr' : x[:-30],
                        'vol_um3' : func(x[:-30], *popt_vol), #np.exp(x[:-30]*slope_basan + intercept_basan), #
                        'dataset' : ['Basan et al. 2015' for i in np.arange(len(x[:-30]))]}, 
                        columns = ['growth_rate_hr', 'vol_um3',
                               'dataset']))
# source_pred = source_pred.append(\
#                 pd.DataFrame({'growth_rate_hr' : x,
#                         'vol_um3' : func(x, *popt_vol_avg), 
#                         'dataset' : ['average' for i in np.arange(len(x))]}, 
#                         columns = ['growth_rate_hr', 'vol_um3',
#                                'dataset']))

In [718]:
l_data = alt.Chart(source_data).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('vol_um3:Q', title = 'cell size (\mu m3)'),
        color = 'dataset:N')
l_pred = alt.Chart(source_pred).mark_line().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('vol_um3:Q', title = 'cell size (\mu m3)'),
        color = 'dataset:N')
l = alt.layer(l_data, l_pred).properties(
        height=300,
        width=300
        )

r_data = alt.Chart(source_data).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('vol_um3:Q', title = 'cell size (\mu m3)',
                  scale = alt.Scale(type='log')),
        color = 'dataset:N')
r_pred = alt.Chart(source_pred).mark_line().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('vol_um3:Q', title = 'cell size (\mu m3)', 
                  scale = alt.Scale(type='log')),
        color = 'dataset:N')
r = alt.layer(r_data, r_pred).properties(
        height=300,
        width=300
        )

(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )



alt.HConcatChart(...)

At first glace the data looks quite concerning. However, the exponent in each dataset is roughly similar. In the Supplemental material of Basan et al., they actually show the comparison of cell lengths and widths between their data and that of Taheri-Araghi et al. An important observation was that while both datasets were predicting similar cell lengths, the cell widths were different and appear to be due this measurement. Specifically, given the limitations in resolution and different computational procedures for segmentation and thresholding, minor differences in the measurement of cell width will have a big effect on total cell size. 

Now for our attempts to 'correct' for disagreement about cell volumes. Since Schmidt et al. used their cell volumes in their attempt to adjust numbers to maintain a constant cellular protein concentration, we need to readjust these based on what we believe might be more accurate values. For now, lets stick to the Si et al. numbers.

In [719]:
source_schmidt = pd.DataFrame(\
                {'protein_conc' :[d.reported_fg_per_cell.sum()/vol_dict[c] for c,d in data.groupby('condition')],
                 'protein_fg' :[d.reported_fg_per_cell.sum() for c,d in data.groupby('condition')],
                'growth_rate_hr' : [d.growth_rate_hr.unique() for c,d in data.groupby('condition')], 
                'label' : ['Schmidt et al. 2016' for i in np.arange(len(data_condition))]},
                             columns = ['protein_conc', 'protein_fg' ,'growth_rate_hr', 'label' ])


schmidt_gr = np.array([lambda_dict[c] for c in data_condition])
pred_vol_Si = (0.28 * np.exp(1.33  * schmidt_gr))
pred_vol_Si_glu = (0.28 * np.exp(1.33  * 0.58))


Si_vol_pred_dict = dict(zip(data_condition, pred_vol_Si))
source_schmidt = source_schmidt.append(pd.DataFrame(\
                {'protein_conc' :[240.0/pred_vol_Si_glu for i in np.arange(len(data_condition))],
                 'protein_fg' : [(240.0/pred_vol_Si_glu) * Si_vol_pred_dict[c] for c in data_condition], 
                  'growth_rate_hr' : schmidt_gr, 
                'label' : ['Recorrect volume using Si et al. 2017' for i in np.arange(len(data_condition))]},
                             columns = ['protein_conc', 'protein_fg' ,'growth_rate_hr', 'label' ]))


l = alt.Chart(source_schmidt).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_conc:Q', title = 'total protein concentration (fg per fL)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

r = alt.Chart(source_schmidt).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_fg:Q', title = 'total protein mass (fg per cell)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )



alt.HConcatChart(...)

In [649]:
data_condition

array(['chemostat_u0.12', 'chemostat_u0.2', 'galactose', 'acetate',
       'chemostat_u0.35', 'pyruvate', 'fumarate', 'succinate',
       'glucosamine', 'mannose', 'glycerol', 'chemostat_u0.5', 'xylose',
       'osmotic_stress_glucose', 'glucose', 'pH6', 'fructose', '42C',
       'glycerol_pAA', 'lb_miller'], dtype=object)

## Correction Approach 2 - Don't assume non-constant protein concentration

Next we need to consider how this relates to total protein and cell mass. From the work of Basan et al. 2015 (from the Hwa lab), they actually show a linear relationship between the total dry mass and cell volume. This suggests that the total mass concentration is constant independent of growth rate. I believe this also suggest that the water mass 'concentration' is also constant. From other work from the Hwa lab (and others), the RNA to total protein ratio is very well characterized. Perhaps Dai et al. 2016 might be the best place to grab this information as a function of growth rate. Let's also make use of the DNA measurements in Basan et al. 2015. 


For this estimation, we will assume that the sum of protein, RNA, and DNA account for 90% of the total cell mass.  



In [720]:
[lambda_dai, R_P_dai] = np.array(\
        [[0.0, 0.08853279947047754],
        [0.03324706890845652, 0.09742834356027935],
        [0.12844176066233703, 0.12157153165470358],
        [0.19652012565308674, 0.12917148174069676],
        [0.23055930814846148, 0.13297145678369332],
        [0.2849547247405284, 0.14694954887503597],
        [0.33601892391911736, 0.15201256530868013],
        [0.4074068045812377, 0.17107537557577435],
        [0.417639175984852, 0.16979497279144085],
        [0.4517000602223341, 0.17104716331103476],
        [0.485674137491387, 0.18249049192423916],
        [0.5503561798423366, 0.1888187199227418],
        [0.6727865579409387, 0.21549233114688282],
        [0.6864152519843529, 0.21548365045003987],
        [0.7000547968988209, 0.21420107749149564],
        [0.7170798135820351, 0.21546411888214323],
        [0.744196140345166, 0.2320073568905744],
        [0.9177883754618401, 0.25227895419304786],
        [0.9448830004828637, 0.27136997672488156],
        [0.9926268331190284, 0.2662440252391261],
        [0.9753630972726335, 0.29300661360590724],
        [1.0979236858238794, 0.3043935176896325],
        [1.1624538159800777, 0.32855623735195344],
        [1.2677832212980895, 0.36288405301735593],
        [1.566952587118931, 0.4404005056505911],
        [1.7949076862145108, 0.4784718718295111]]).T


slope_dia_RP_A, intercept_dia_RP_A, r_value, p_value, std_err = stats.linregress(lambda_dai[:14], 
                                            R_P_dai[:14])
slope_dia_RP_B, intercept_dia_RP_B, r_value, p_value, std_err = stats.linregress(lambda_dai[14:], 
                                            R_P_dai[14:])


# DNA measurements from Basan et al. 2015, growth rate (hr-1), dna (femtogram per cell)
lambda_basan_dna = [0.42, 0.45, 0.7, 0.98, 1.27, 1.84] 
dna_basan = 1E15*np.divide(1E-6*np.array([16.5, 14.2, 14.1, 11.9, 11.3, 11.1]), 
                      1E8*np.array([19.4, 17.1, 16.0, 10.7, 7.93, 3.43]))


In [721]:
# Take a look at DNA mass data and fit to exponential
source_dna_data = pd.DataFrame({'growth_rate_hr' : lambda_basan_dna,
                       'dna_pg' : dna_basan},
                     columns = ['growth_rate_hr', 'dna_pg'])

dna_data = alt.Chart(source_dna_data).mark_point().encode(
        x = 'growth_rate_hr',
        y = alt.Y('dna_pg'))

#### perform fit

popt_dna, pcov_dan = curve_fit(func, lambda_basan_dna, dna_basan, p0=(1, 1e-6, 1))
x = np.linspace(0,2,100)

source_dna_pred = pd.DataFrame({'growth_rate_hr' : x,
                       'dna_pg_pred' : func(x, *popt_dna)},
                     columns = ['growth_rate_hr', 'dna_pg_pred'])

dna_pred = alt.Chart(source_dna_pred).mark_line().encode(
        x = 'growth_rate_hr',
        y = alt.Y('dna_pg_pred', title = 'DNA mass (fg per cell)'))

alt.layer(dna_data, dna_pred).properties(
        height=300,
        width=300
        ).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )



alt.LayerChart(...)

In [725]:
schmidt_gr = np.array([lambda_dict[c] for c in data_condition])
pred_vol_Si = (0.28 * np.exp(1.33  * schmidt_gr))
# pred_vol_Si = func(schmidt_gr, *popt_vol_avg)
pred_drymass_Si = ((1.15*0.35)*(pred_vol_Si*1E-12)*1E15)

pred_dnamass_Si =  func(schmidt_gr, *popt_dna)
pred_RNA_protein_mass_Si = pred_drymass_Si*0.90 - pred_dnamass_Si

#### predict RNA/Protein ratio:
pred_RNA_protein_ratio = np.append(\
                    (slope_dia_RP_A*schmidt_gr[:-2] + intercept_dia_RP_A),
                    (slope_dia_RP_B*schmidt_gr[-2:] + intercept_dia_RP_B))


pred_RNAmass_Si = (pred_RNA_protein_ratio * pred_RNA_protein_mass_Si) / (1+ pred_RNA_protein_ratio)
pred_proteinmass_Si =  (pred_RNA_protein_mass_Si/ (1+pred_RNA_protein_ratio))




In [726]:
# Take a look at DNA mass data and fit to exponential
source_Si_conc_pred = pd.DataFrame()
source_Si_conc_pred = pd.DataFrame({'growth_rate_hr' : schmidt_gr,
                        'mass' : pred_dnamass_Si,
                       'conc' : pred_dnamass_Si / pred_vol_Si, 
                       'label' : ['dna' for i in np.arange(len(schmidt_gr))]},
                     columns = ['growth_rate_hr', 'mass', 'conc',
                               'label'])

source_Si_conc_pred = source_Si_conc_pred.append(\
                      pd.DataFrame({'growth_rate_hr' : schmidt_gr,
                       'mass' : pred_proteinmass_Si,
                       'conc' : (pred_proteinmass_Si / pred_vol_Si), 
                       'label' : ['protein' for i in np.arange(len(schmidt_gr))]},
                     columns = ['growth_rate_hr', 'mass', 'conc',
                               'label']))

source_Si_conc_pred = source_Si_conc_pred.append(\
                      pd.DataFrame({'growth_rate_hr' : schmidt_gr,
                       'mass' : pred_RNAmass_Si,
                       'conc' : pred_RNAmass_Si / pred_vol_Si, 
                       'label' : ['rna' for i in np.arange(len(schmidt_gr))]},
                     columns = ['growth_rate_hr', 'mass', 'conc',
                               'label']))

l = alt.Chart(source_Si_conc_pred).mark_point().encode(
        x = 'growth_rate_hr',
        y = alt.Y('conc', title = 'concentration (pg/fL)'),
        color = 'label').properties(
        height=300,
        width=300
        )

r = alt.Chart(source_Si_conc_pred).mark_point().encode(
        x = 'growth_rate_hr',
        y = alt.Y('mass', title = 'total mass (pg per cell)'),
        color = 'label').properties(
        height=300,
        width=300
        )


(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )

alt.HConcatChart(...)

The absolute value of the total protein per cell is a bit low; likely related to the estimate of cell volume by Si et al. (my best guess, if 240 fg per cell for glucose condition is correct). Here we make a further correction to the Schmidt data by assuming the protein concentration varies as predicted here. 

In [731]:
schmidt_gr = np.array([lambda_dict[c] for c in data_condition])
pred_vol_Si = (0.28 * np.exp(1.33  * schmidt_gr))
pred_vol_Si_glu = (0.28 * np.exp(1.33  * 0.58))


Si_vol_pred_dict = dict(zip(data_condition, pred_vol_Si))
source_schmidt = source_schmidt.append(pd.DataFrame(\
#                 {'protein_conc' :(pred_proteinmass_Si*1.29) / pred_vol_Si,
#                  'protein_fg' : (pred_proteinmass_Si*1.29), 
                {'protein_conc' :(pred_proteinmass_Si) / pred_vol_Si,
                 'protein_fg' : (pred_proteinmass_Si), 
                  'growth_rate_hr' : schmidt_gr, 
                'label' : ['Recorrect with non-constant protein concentration' for i in np.arange(len(pred_vol_Si))]},
                             columns = ['protein_conc', 'protein_fg' ,'growth_rate_hr', 'label' ]))


l = alt.Chart(source_schmidt).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_conc:Q', title = 'total protein concentration (fg per fL)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

r = alt.Chart(source_schmidt).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_fg:Q', title = 'total protein mass (fg per cell)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )




alt.HConcatChart(...)

# Correction Approach 3. 

Assume the total mass should follow the values measured independently in Basan et al. as a function of growth rate. This seems like a nice alternative way to try to do the correction so that we can see how much the numbers might change.

I grabbed data from Appendix Figure S7 for nutrient limitation. X axis is growth rate (hr-1), while Y axis is total protein per cell (pg/cell). 


In [728]:
[ lambda_pg, pg_cell ]= np.array([[0.4201720300298032, 0.20177311653525498],
                    [0.4522767570830345, 0.22318632813973682],
                    [0.7005130720187119, 0.2242426528841439],
                    [0.9850039612177915, 0.3148149545403105],
                    [1.2836797826989095, 0.4054476176104427],
                    [1.8311955332553662, 0.9652242803787682]]).T

popt_pg, pcov_pg = curve_fit(func, lambda_pg, pg_cell, p0=(1, 1e-6, 1))



In [729]:
source_data = pd.DataFrame({'growth_rate_hr' : lambda_pg,
                       'cell_mass_pg' : pg_cell*1000},
                     columns = ['growth_rate_hr', 'cell_mass_pg'])
source_pred = pd.DataFrame({'growth_rate_hr' : x,
                       'cell_mass_pg' : func(x, *popt_pg)*1000},
                     columns = ['growth_rate_hr', 'cell_mass_pg'])

basan_data = alt.Chart(source_data).mark_point().encode(
        x = 'growth_rate_hr',
        y = alt.Y('cell_mass_pg')).properties(
        height=300,
        width=300
        )

basan_pred = alt.Chart(source_pred).mark_line().encode(
        x = alt.X('growth_rate_hr', title = 'growth rate (hr-1)'),
        y = alt.Y('cell_mass_pg', title = 'protein mass (fg per cell)')).properties(
        height=300,
        width=300
        )

alt.layer(basan_data, basan_pred).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )


alt.LayerChart(...)

In [730]:
schmidt_gr = np.array([lambda_dict[c] for c in data_condition])
pred_vol_Si = (0.28 * np.exp(1.33  * schmidt_gr))
pred_vol_Si_glu = (0.28 * np.exp(1.33  * 0.58))


Si_vol_pred_dict = dict(zip(data_condition, pred_vol_Si))
source = pd.DataFrame(\
                {'protein_conc' :(func(schmidt_gr, *popt_pg)*1000) / pred_vol_Si,
                 'protein_fg' : func(schmidt_gr, *popt_pg)*1000, 
                  'growth_rate_hr' : schmidt_gr, 
                 'label' : ['Correction based on Basan et al.' for i in np.arange(len(schmidt_gr))]},
                      columns = ['protein_conc', 'protein_fg' ,'growth_rate_hr', 'label'])


source = source.append(pd.DataFrame(\
                {'protein_conc' :[d.reported_fg_per_cell.sum()/vol_dict[c] for c,d in data.groupby('condition')],
                 'protein_fg' :[d.reported_fg_per_cell.sum() for c,d in data.groupby('condition')],
                'growth_rate_hr' : [d.growth_rate_hr.unique() for c,d in data.groupby('condition')], 
                'label' : ['Schmidt et al. 2016' for i in np.arange(len(data_condition))]},
                             columns = ['protein_conc', 'protein_fg' ,'growth_rate_hr', 'label' ]))

l = alt.Chart(source).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_conc:Q', title = 'total protein concentration (fg per fL)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

r = alt.Chart(source).mark_point().encode(
        x = alt.X('growth_rate_hr:Q', title = 'growth rate (hr-1)'),
        y = alt.Y('protein_fg:Q', title = 'total protein mass (fg per cell)'),
        color = 'label:N').properties(
        height=300,
        width=300
        )

(l | r).configure_axis(
    labelFontSize=16,
    titleFontSize=16,
       )




alt.HConcatChart(...)